In [1]:
import json
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk

In [2]:
_index = "music_data"
es = Elasticsearch("http://127.0.0.1:9200")

In [3]:
node_mappings = {
    "mappings": {
        "properties": {
            "geci": {  # field: 歌词内容
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
            "song": {  # field: 歌曲名称
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
            "album": {  # field: 歌词所属专辑
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
            "singer": {  # field: 歌手
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
            "composer": {  # field: 歌手
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
            "author": {  # field: 歌手
                "type": "text",  # lxw NOTE: cannot be string
                "analyzer": "ik_max_word",
                "search_analyzer": "ik_smart",
                "index": "true"  # The index option controls whether field values are indexed.
            },
        }
    }
}

In [4]:
es.indices.create(index=_index, body=node_mappings)

C:\Users\Administrator\Envs\py3.6.5_base\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: The 'body' parameter is deprecated and will be removed in a future version. Instead use individual parameters.
  """Entry point for launching an IPython kernel.


ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'music_data'})

In [5]:
index = 0
count = 0
action_list = []
BULK_COUNT = 2000  # 每BULK_COUNT个句子一起插入到ES中

In [15]:
import time
import json

In [16]:
start_time = time.time()

In [17]:
'''批量插入数据'''


def insert_data_bulk(action_list):
    success, _ = bulk(es, action_list, index=_index, raise_on_error=True)
    print("Performed {0} actions. _: {1}".format(success, _))

In [19]:
with open("./data/music.json", "r", encoding="utf-8") as f:
    tmp = f.readlines()
    print(len(tmp))
    for line in tmp:
        if not line:
            continue
        item = json.loads(line)
        index += 1

        action = {
            "_index": _index,
            "_source": {
                "song": item["song"],
                "singer": item['singer'],
                "album": item['album'],
                "geci": '\n'.join(item['geci']),
                "compser": item['composer'],
                "author": item['author']
            }
        }

        action_list.append(action)

        if index > BULK_COUNT:
            insert_data_bulk(action_list=action_list)
            index = 0
            count += 1
            print(count)
            action_list = []

        end_time = time.time()
        print("Time Cost:{0}".format(end_time - start_time))

140068
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.11700081825256
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.1179690361023
Time Cost:99.

In [21]:
'''根据title进行事件的匹配查询'''
def search_specific(self, value, key="name"):
    query_body = {
        "query": {
            "match": {
                key: value,
            }
        }
    }
    searched = self.es.search(index=_index, body=query_body, size=100)
    # 输出查询到的结果
    return searched["hits"]["hits"]

C:\Users\Administrator\Envs\py3.6.5_base\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: The 'body' parameter is deprecated and will be removed in a future version. Instead use individual parameters.
  


ObjectApiResponse({'took': 1, 'timed_out': False, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}, 'hits': {'total': {'value': 0, 'relation': 'eq'}, 'max_score': None, 'hits': []}})

In [26]:
query_body = {
    "query": {
        "match": {
            "song": "玫瑰的名字",
        }
    }
}
es.search(index=_index, body=query_body, size=100)["hits"]["hits"]

C:\Users\Administrator\Envs\py3.6.5_base\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: The 'body' parameter is deprecated and will be removed in a future version. Instead use individual parameters.
  


[{'_index': 'music_data',
  '_id': 'Ospqf4MBfkgpXchlxW55',
  '_score': 16.2716,
  '_source': {'song': '玫瑰的名字',
   'singer': '张雨生',
   'album': '《口是心非》',
   'geci': '玫瑰多情也多刺竟与奶似曾相识\n有多少次我尝试写首诗留下你那婀娜多姿的样子\n有时候娇横伤人有时候娇柔依人\n我只能用最奢侈的玻璃为你筑起不惧风雨的天地\n只要能够陪着你我都愿意我就是你忠实的园丁\n只要能够想着你我就欢喜\n即使你宁可自由自在呼吸那一窗星星\n名字背过又忘记符号充满了神秘\n原在梦里忽而又中世纪我像圣堂下为你禁欲的僧侣',
   'compser': '',
   'author': ''}},
 {'_index': 'music_data',
  '_id': '4spqf4MBfkgpXchlyXZv',
  '_score': 10.585005,
  '_source': {'song': '名字',
   'singer': '黄安',
   'album': '《妹妹我爱你》',
   'geci': '从此就有许多心事\n小心看着礼仪廉耻\n有做不完的事\n放不下的面子\n那只是因为我\n世上的人一模样\n一口气来一柱香\n红尘中来一较长短\n我出尽洋相\n我变化无常\n我给你三两三\n我陪你上梁山\n你追不追得上\n在午夜梦回 想一想\n赢了或是输了\n又怎样\n啊……\n现在过了一年又一年\n岁月改变我的容颜\n有钱不如令人怀念\n这快乐有限\n这痛苦无边\n这就是我的缘\n○The End○',
   'compser': '黄安',
   'author': '黄安'}},
 {'_index': 'music_data',
  '_id': 'Pspqf4MBfkgpXchlz4q2',
  '_score': 10.585005,
  '_source': {'song': '名字',
   'singer': '张智成',
   'album': '《May I Love U》',
   'geci': '寂寞飞过城市的上空\n人害怕脆弱只能够\n用忙碌带过\n冷漠停在交通阻塞的街头\n人们的问